# Data Olympics - an ipyvizzu-story
## [Documentation](https://ipyvizzu-story.vizzuhq.com/)

In [1]:
#!pip install ipyvizzu --upgrade
#!pip install ipyvizzu-story --upgrade

In [2]:
# Import components, add data to pandas data frame

import pandas as pd
import numpy as np 
from ipyvizzu import Data, Config, Style
from ipyvizzustory import Story, Slide, Step

In [3]:
data_hosts_path = '../data/olympic_hosts.csv'
data_medals_path = '../data/olympic_medals.csv'
data_results_path = '../data/olympic_results.csv'
data_athletes_path = '../data/olympic_athletes.csv'

In [4]:
df_hosts = pd.read_csv(data_hosts_path)
df_medals = pd.read_csv(data_medals_path)
df_results = pd.read_csv(data_results_path)
df_athletes = pd.read_csv(data_athletes_path)

In [5]:
data = df_medals.merge(df_hosts, how='left', left_on='slug_game', right_on='game_slug')
data['athlete_full_name'] = data['athlete_full_name'].str.title()
# removes join columns
data.drop(['slug_game', 'game_slug'], inplace=True, axis=1)
# removes unused columns
data.drop(['game_end_date', 'game_start_date'], axis=1, inplace=True)

In [6]:
df_medals.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 21697 entries, 0 to 21696
Data columns (total 12 columns):
 #   Column                 Non-Null Count  Dtype 
---  ------                 --------------  ----- 
 0   discipline_title       21697 non-null  object
 1   slug_game              21697 non-null  object
 2   event_title            21697 non-null  object
 3   event_gender           21697 non-null  object
 4   medal_type             21697 non-null  object
 5   participant_type       21697 non-null  object
 6   participant_title      6584 non-null   object
 7   athlete_url            17027 non-null  object
 8   athlete_full_name      18073 non-null  object
 9   country_name           21697 non-null  object
 10  country_code           20195 non-null  object
 11  country_3_letter_code  21697 non-null  object
dtypes: object(12)
memory usage: 2.0+ MB


In [7]:
# replaces long country names with short analogs
country_dict = {
    'German Democratic Republic (Germany)':'Germany', 
    'Federal Republic of Germany':'Germany',
    "Democratic People's Republic of Korea":'North Korea',
    "Republic of Korea":"South Korea",
    "People's Republic of China":'China',
    "Islamic Republic of Iran":'Iran',
    "United States of America":'USA'}
data['country_name'] = data['country_name'].replace(country_dict)

In [8]:
# replaces changed disciplines names
discipline_map={
    "Gymnastics Artistic":"Artistic Gymnastics",
    "Gymnastics Rhythmic":"Rhythmic Gymnastics",
    "Synchronized Swimming":"Artistic Swimming",
    "Equestrian Dressage":"Equestrian",
    "Equestrian Jumping":"Equestrian",
    "Equestrian Eventing":"Equestrian",
    "Trampoline":"Trampoline Gymnastics",
    "Cycling BMX":"Cycling BMX Racing",
    "Short Track Speed Skating": "Short Track"
}
data['discipline_title'] = data['discipline_title'].replace(discipline_map)

In [9]:
data_athlete = data[data['participant_type']=='Athlete']
data_athlete.shape

(15113, 15)

In [10]:
data_team = data[data['participant_type']=='GameTeam']
data_team.shape

(6584, 15)

In [11]:
data_team_a = data_team[data_team['athlete_full_name'].isna()]
data_team_a.shape

(3624, 15)

In [12]:
group_columns = ['discipline_title', 'event_title', 'event_gender', 'medal_type', 'participant_type', 'participant_title',
                 'country_name', 'country_3_letter_code', 'game_location', 'game_season', 'game_name', 'game_year']
agg_columns = ['country_code', 'athlete_full_name']
data_team_b = data_team[data_team['athlete_full_name'].notna()].groupby(group_columns)[agg_columns]\
                                                               .agg(lambda x: set(x)).reset_index()
data_team_b['country_code'] = data_team_b['country_code'].apply(lambda x: list(x)[0])
data_team_b['athlete_full_name'] = data_team_b['athlete_full_name'].apply(lambda x: list(x))
data_team_b.shape

(1480, 14)

In [13]:
data_medal = pd.concat([data_team_a, data_team_b, data_athlete], axis=0).reset_index(drop=True)
#data_medal = data
data_medal['game_year'] = data_medal['game_year'].astype(str)
data_medal.shape

(20217, 15)

In [14]:
# fix some disciplines and events
data_medal.loc[data_medal['event_title']=='Baseball', 'discipline_title'] = 'Baseball'
data_medal.loc[data_medal['event_title']=='Softball', 'discipline_title'] = 'Softball'
data_medal.loc[data_medal['event_title']=='Baseball', 'event_title'] = 'baseball men'
data_medal.loc[data_medal['event_title']=='Softball', 'event_title'] = 'softball women'

data_medal.loc[data_medal['event_title']=='rugby-7 men', 'discipline_title'] = 'Rugby Sevens'
data_medal.loc[data_medal['event_title']=='rugby-7 women', 'discipline_title'] = 'Rugby Sevens'
data_medal.loc[data_medal['event_title']=='rugby-7 men', 'event_title'] = 'Men'
data_medal.loc[data_medal['event_title']=='rugby-7 women', 'event_title'] = 'Women'

In [15]:
# Add count to dataframe
data_medal.insert(0,'Count',pd.Series([1 for x in range(len(data_medal.index))]))

In [16]:
df2 = data_medal.groupby(['game_season','discipline_title'],sort=True)['medal_type'].count().sort_values()
df2.tail(12)


game_season  discipline_title   
Summer       Canoe Sprint            568
             Judo                    607
Winter       Speed skating           611
Summer       Fencing                 668
             Weightlifting           679
             Rowing                  808
             Shooting                862
             Boxing                  996
             Artistic Gymnastics    1021
             Wrestling              1356
             Swimming               1763
             Athletics              3080
Name: medal_type, dtype: int64

In [17]:
df3 = data_medal.groupby(['game_season','country_name'],sort=True)['medal_type'].count().sort_values()
df3.tail(12)

game_season  country_name 
Winter       Germany           435
Summer       Sweden            495
             Japan             497
             Hungary           509
             Australia         547
             Italy             615
             China             634
             France            744
             Great Britain     913
             Soviet Union     1010
             Germany          1373
             USA              2627
Name: medal_type, dtype: int64

In [18]:
df4 = data_medal.groupby(['game_season','country_name'],sort=True)['medal_type'].count().sort_values()
df4.tail(12)

game_season  country_name 
Winter       Germany           435
Summer       Sweden            495
             Japan             497
             Hungary           509
             Australia         547
             Italy             615
             China             634
             France            744
             Great Britain     913
             Soviet Union     1010
             Germany          1373
             USA              2627
Name: medal_type, dtype: int64

In [19]:
# create a list of our conditions


conditions = [
    (data_medal['discipline_title'] == 'Athletics'),
    (data_medal['discipline_title'] == 'Swimming'),
    (data_medal['discipline_title'] == 'Wrestling'),
    (data_medal['discipline_title'] == 'Artistic Gymnastics'),
    (data_medal['discipline_title'] == 'Boxing'),
    (data_medal['discipline_title'] == 'Shooting'),
    (data_medal['discipline_title'] == 'Rowing'),
    (data_medal['discipline_title'] == 'Weightlifting'),
    (data_medal['discipline_title'] == 'Fencing'),
    (data_medal['discipline_title'] == 'Judo'),
    ]

# create a list of the values we want to assign for each condition
values = ['Athletics', 'Swimming', 'Wrestling', 'Artistic Gymnastics', 'Boxing', 'Shooting', 'Rowing', 'Weightlifting', 'Fencing', 'Judo']
horizontal = ['1','2','3','4','5','1','2','3','4','5']
vertical = ['1','1','1','1','1','2','2','2','2','2']
# create a new column and use np.select to assign values to it using our lists as arguments
data_medal['top10'] = np.select(conditions, values)
data_medal['top10'] = data_medal['top10'].replace(['0'], 'Other')
data_medal['horizontal'] = np.select(conditions,horizontal)
data_medal['vertical'] = np.select(conditions,vertical)
data_medal['horizontal'] = data_medal['horizontal'].astype(str)
data_medal['vertical'] = data_medal['vertical'].astype(str)
display(data_medal)

Count discipline_title                      event_title event_gender  \
0          1          Curling                            Women        Women   
1          1          Curling                            Women        Women   
2          1          Curling                            Women        Women   
3          1          Curling                              Men          Men   
4          1          Curling                              Men          Men   
...      ...              ...                              ...          ...   
20212      1    Weightlifting  heavyweight - one hand lift men          Men   
20213      1    Weightlifting  heavyweight - one hand lift men          Men   
20214      1    Weightlifting  heavyweight - two hand lift men          Men   
20215      1    Weightlifting  heavyweight - two hand lift men          Men   
20216      1    Weightlifting  heavyweight - two hand lift men          Men   

      medal_type participant_type participant_title  \
0           GOLD         GameTeam     Great Britain   
1         SILVER         GameTeam             Japan   
2         BRONZE         GameTeam            Sweden   
3           GOLD         GameTeam            Sweden   
4         SILVER         GameTeam     Great Britain   
...          ...              ...               ...   
20212     SILVER          Athlete               NaN   
20213     BRONZE          Athlete               NaN   
20214       GOLD          Athlete               NaN   
20215     SILVER          Athlete               NaN   
20216     BRONZE          Athlete               NaN   

                                             athlete_url  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
20212      https://olympics.com/en/athletes/viggo-jensen   
20213                                                NaN   
20214      https://olympics.com/en/athletes/viggo-jensen   
20215  https://olympics.com/en/athletes/launceston-el...   
20216   https://olympics.com/en/athletes/sotirios-versis   

             athlete_full_name   country_name country_code  \
0                          NaN  Great Britain           GB   
1                          NaN          Japan           JP   
2                          NaN         Sweden           SE   
3                          NaN         Sweden           SE   
4                          NaN  Great Britain           GB   
...                        ...            ...          ...   
20212             Viggo Jensen        Denmark           DK   
20213  Alexandros Nikolopoulos         Greece           GR   
20214             Viggo Jensen        Denmark           DK   
20215        Launceston Elliot  Great Britain           GB   
20216          Sotirios Versis         Greece           GR   

      country_3_letter_code game_location     game_name game_season game_year  \
0                       GBR         China  Beijing 2022      Winter      2022   
1                       JPN         China  Beijing 2022      Winter      2022   
2                       SWE         China  Beijing 2022      Winter      2022   
3                       SWE         China  Beijing 2022      Winter      2022   
4                       GBR         China  Beijing 2022      Winter      2022   
...                     ...           ...           ...         ...       ...   
20212                   DEN        Greece   Athens 1896      Summer      1896   
20213                   GRE        Greece   Athens 1896      Summer      1896   
20214                   DEN        Greece   Athens 1896      Summer      1896   
20215                   GBR        Greece   Athens 1896      Summer      1896   
20216                   GRE        Greec

In [20]:
# create a list of our conditions


conditions2 = [
    (data_medal['country_name'] == 'USA'),
    (data_medal['country_name'] == 'Germany'),
    (data_medal['country_name'] == 'Soviet Union'),
    (data_medal['country_name'] == 'Great Britain'),
    (data_medal['country_name'] == 'France'),
    (data_medal['country_name'] == 'China'),
    (data_medal['country_name'] == 'Italy'),
    (data_medal['country_name'] == 'Australia'),
    (data_medal['country_name'] == 'Hungary'),
    (data_medal['country_name'] == 'Japan'),
    ]

# create a list of the values we want to assign for each condition
values2 = ['USA', 'Germany', 'Soviet Union', 'Great Britain', 'France', 'China', 'Italy', 'Australia', 'Hungary', 'Japan']
# create a new column and use np.select to assign values to it using our lists as arguments
data_medal['top10C'] = np.select(conditions2, values2)
data_medal['top10C'] = data_medal['top10C'].replace(['0'], 'Other')
display(data_medal)

Count discipline_title                      event_title event_gender  \
0          1          Curling                            Women        Women   
1          1          Curling                            Women        Women   
2          1          Curling                            Women        Women   
3          1          Curling                              Men          Men   
4          1          Curling                              Men          Men   
...      ...              ...                              ...          ...   
20212      1    Weightlifting  heavyweight - one hand lift men          Men   
20213      1    Weightlifting  heavyweight - one hand lift men          Men   
20214      1    Weightlifting  heavyweight - two hand lift men          Men   
20215      1    Weightlifting  heavyweight - two hand lift men          Men   
20216      1    Weightlifting  heavyweight - two hand lift men          Men   

      medal_type participant_type participant_title  \
0           GOLD         GameTeam     Great Britain   
1         SILVER         GameTeam             Japan   
2         BRONZE         GameTeam            Sweden   
3           GOLD         GameTeam            Sweden   
4         SILVER         GameTeam     Great Britain   
...          ...              ...               ...   
20212     SILVER          Athlete               NaN   
20213     BRONZE          Athlete               NaN   
20214       GOLD          Athlete               NaN   
20215     SILVER          Athlete               NaN   
20216     BRONZE          Athlete               NaN   

                                             athlete_url  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
20212      https://olympics.com/en/athletes/viggo-jensen   
20213                                                NaN   
20214      https://olympics.com/en/athletes/viggo-jensen   
20215  https://olympics.com/en/athletes/launceston-el...   
20216   https://olympics.com/en/athletes/sotirios-versis   

             athlete_full_name   country_name country_code  \
0                          NaN  Great Britain           GB   
1                          NaN          Japan           JP   
2                          NaN         Sweden           SE   
3                          NaN         Sweden           SE   
4                          NaN  Great Britain           GB   
...                        ...            ...          ...   
20212             Viggo Jensen        Denmark           DK   
20213  Alexandros Nikolopoulos         Greece           GR   
20214             Viggo Jensen        Denmark           DK   
20215        Launceston Elliot  Great Britain           GB   
20216          Sotirios Versis         Greece           GR   

      country_3_letter_code game_location     game_name game_season game_year  \
0                       GBR         China  Beijing 2022      Winter      2022   
1                       JPN         China  Beijing 2022      Winter      2022   
2                       SWE         China  Beijing 2022      Winter      2022   
3                       SWE         China  Beijing 2022      Winter      2022   
4                       GBR         China  Beijing 2022      Winter      2022   
...                     ...           ...           ...         ...       ...   
20212                   DEN        Greece   Athens 1896      Summer      1896   
20213                   GRE        Greece   Athens 1896      Summer      1896   
20214                   DEN        Greece   Athens 1896      Summer      1896   
20215                   GBR        Greece   Athens 1896      Summer      1896   
20216                   GRE        Greec

In [21]:
data_medal.dtypes

Count                     int64
discipline_title         object
event_title              object
event_gender             object
medal_type               object
participant_type         object
participant_title        object
athlete_url              object
athlete_full_name        object
country_name             object
country_code             object
country_3_letter_code    object
game_location            object
game_name                object
game_season              object
game_year                object
top10                    object
horizontal               object
vertical                 object
top10C                   object
dtype: object

In [22]:
#sort the dataframe by top countries
countrysorter = ['USA', 'Germany', 'Soviet Union', 'Great Britain', 'France', 'China', 'Italy', 'Australia', 'Hungary', 'Japan', 'Other']
# Create the dictionary that defines the order for sorting
sorterIndex = dict(zip(countrysorter, range(len(countrysorter))))
# Generate a rank column that will be used to sort
# the dataframe numerically
data_medal['Country_Rank'] = data_medal['country_name'].map(sorterIndex)
# the actual sorting is done together with salary, title below

#sort the dataframe by year
yearsorter = ['1896', '1900', '1904', '1908', '1912', '1916', '1920', '1924', '1928', '1932', '1936', '1940', '1944', '1948', '1952', '1956', '1960', '1964', '1968', '1972', '1976', '1980', '1984', '1988', '1992', '1994', '1996', '1998', '2000', '2002', '2004', '2006', '2008', '2010', '2012', '2014', '2016', '2018', '2020', '2022']
# Create the dictionary that defines the order for sorting
yearIndex = dict(zip(yearsorter, range(len(yearsorter))))
# Generate a rank column that will be used to sort
# the dataframe numerically
data_medal['Year_Rank'] = data_medal['game_year'].map(yearIndex)
# the actual sorting is done together with salary, title below

#sort the dataframe by year
gendersorter = ['Women','Men','Mixed','Open']
# Create the dictionary that defines the order for sorting
genderIndex = dict(zip(gendersorter, range(len(gendersorter))))
# Generate a rank column that will be used to sort
# the dataframe numerically
data_medal['Gender_Rank'] = data_medal['event_gender'].map(genderIndex)
# the actual sorting is done together with salary, title below


#sort the dataframe by year
medalsorter = ['BRONZE','SILVER','GOLD']
# Create the dictionary that defines the order for sorting
medalIndex = dict(zip(medalsorter, range(len(medalsorter))))
# Generate a rank column that will be used to sort
# the dataframe numerically
data_medal['Medal_Rank'] = data_medal['medal_type'].map(medalIndex)
# the actual sorting is done together with salary, title below


#sorting based on all of the rankings
data_medal.sort_values(['Country_Rank','Year_Rank','Gender_Rank','Medal_Rank'], inplace = True)

#display(data_medal)
data_medal['Gender_Rank'].unique()

array([1, 0, 3, 2], dtype=int64)

In [23]:
data_medal.loc[data_medal['discipline_title']=='Artistic Gymnastics', 'discipline_title'] = 'Art. Gymn.'
data_medal.loc[data_medal['discipline_title']=='Weightlifting', 'discipline_title'] = 'Weightl.'

In [24]:
data = Data()
data.add_df(data_medal)

In [25]:
data_medal.to_csv('Data Olympics.csv')

In [26]:
df = data_medal.loc[data_medal['event_gender'] == 'Open']
df = df.loc[df['participant_type']== 'Athlete']
df.discipline_title	.unique()
display(df)

Count discipline_title                                 event_title  \
17413      1          Sailing                         firefly class mixed   
16682      1          Sailing  Finn - One Person Dinghy (Heavyweight) men   
15732      1          Sailing  Finn - One Person Dinghy (Heavyweight) men   
15624      1       Equestrian                            individual mixed   
15333      1         Shooting        50m rifle 3 positions 3x40 shots men   
...      ...              ...                                         ...   
7397       1       Equestrian                    Jumping Individual mixed   
6396       1       Equestrian                    Jumping Individual mixed   
6395       1       Equestrian                    Jumping Individual mixed   
5845       1       Equestrian                          Jumping Individual   
5847       1       Equestrian                          Jumping Individual   

      event_gender medal_type participant_type participant_title  \
17413         Open     SILVER          Athlete               NaN   
16682         Open     BRONZE          Athlete               NaN   
15732         Open     SILVER          Athlete               NaN   
15624         Open     BRONZE          Athlete               NaN   
15333         Open     SILVER          Athlete               NaN   
...            ...        ...              ...               ...   
7397          Open       GOLD          Athlete               NaN   
6396          Open     BRONZE          Athlete               NaN   
6395          Open     SILVER          Athlete               NaN   
5845          Open     BRONZE          Athlete               NaN   
5847          Open     SILVER          Athlete               NaN   

                                             athlete_url  \
17413  https://olympics.com/en/athletes/ralph-liggett...   
16682       https://olympics.com/en/athletes/john-marvin   
15732  https://olympics.com/en/athletes/peter-jones-b...   
15624  https://olympics.com/en/athletes/michael-owen-...   
15333  https://olympics.com/en/athletes/john-henry-wr...   
...                                                  ...   
7397      https://olympics.com/en/athletes/steve-guerdat   
6396        https://olympics.com/en/athletes/eric-lamaze   
6395   https://olympics.com/en/athletes/peder-fredricson   
5845   https://olympics.com/en/athletes/maikel-van-de...   
5847   https://olympics.com/en/athletes/peder-fredricson   

             athlete_full_name country_name  ... game_season game_year  \
17413  Ralph Liggett Jr. Evans          USA  ...      Summer      1948   
16682              John Marvin          USA  ...      Summer      1956   
15732      Peter Jones Barrett          USA  ...      Summer      1964   
15624        Michael Owen Page          USA  ...      Summer      1968   
15333        John Henry Writer          USA  ...      Summer      1968   
...                        ...          ...  ...         ...       ...   
7397             Steve Guerdat  Switzerland  ...      Summer      2012   
6396               Eric Lamaze       Canada  ...      Summer      2016   
6395          Peder Fredricson       Sweden  ...      Summer      2016   
5845    Maikel Van Der Vleuten  Netherlands  ...      Summer      2020   
5847          Peder Fredricson       Sweden  ...      Summer      2020   

          top10 horizontal vertical top10C Country_Rank Year_Rank Gender_Rank  \
17413     Other          0        0    USA          0.0        13           3   
16682     Other          0        0    USA          0.0        15           3   
15732     Other          0        0    USA          0.0        17           3   
15624     Other          0        0    USA          0.0        18           3   
15333  Shooting          1        2    USA          0.0        18           3   
...         ...        ...      ...    ...          ...       ...         ...   
7397      Other          0        0  Other          NaN        34           3   
6396   

In [27]:
# Set the style of the charts in the story

style = Style(
    {
        'logo' : {'width' : '5'},
        'title' : {'fontSize' : '3em'},
        'legend' : {'label' : { 'fontSize' : '1.6em'}, 'width': '12em'},
        'plot': {
            'marker' :{ 'label' :{ 'maxFractionDigits' : '1','fontSize':'3em'},
                        'colorPalette' : '#A2A2B2'},
            'yAxis': {
                'label': {
                    'fontSize': '1em',
                    'paddingRight': '1.2em',
                },
                'title': {'color': '#ffffff00'},
            },
            'xAxis': {
                'label': {
                    'angle': '2.5',
                    'fontSize': '1.1em',
                },
                'title': {'color' : '#99999900'},
            },
        },
    }
)

In [28]:
# Create Story object, set size

story = Story(data=data, style=style)
story.set_size('100%', '400px')
story.vizzu_story ="./vizzu-story.min.js"

slide0 = Slide(
    Step(
        Config(
            {
                'size': 'Count',
                'label': 'Count',
                'geometry': 'circle',
                'title': 'All Olympic Medals',
            }
        )
    )
)
story.add_slide(slide0)

slide0_1 = Slide()

slide0_1.add_step(
    Step(
        Config(
            {
                'size': ['discipline_title','top10','Count'],
                'color': 'top10',
                'legend':None,
            }
        ),
                Style({'plot' : {'marker' : { 'colorPalette' : None, 'label':{'fontSize': '1.2em'}}}})
    )
)

slide0_1.add_step(
    Step(
        Data.filter("record.top10 !== 'Other'"),
        Config(
            {
            'label': ['discipline_title'],
                'title': 'Top 10 Disciplines in No. of Medals',
            }
        )
    )
)
story.add_slide(slide0_1)


slide0_2 = Slide() 

slide0_2.add_step(
    Step(
        Data.filter(None),
    )
)

slide0_2.add_step(
    Step(
        Data.filter(None),
        Config(
            {
                'size': 'Count',
                'color': None,
                'label': 'Count',
                'title': 'All Olympic Medals',
            }
        ),
        Style({'plot' : {'marker' : { 'colorPalette' : '#A2A2B2'}}})
    )
)

slide0_2.add_step(
    Step(
        Style({'plot' : {'marker' : { 'label': {'fontSize':'3em'}}}})
    )
)
story.add_slide(slide0_2)

slide1 = Slide()

slide1.add_step(
    Step(
        Config(
            {
                'size': ['game_year','Count'],
            }
        ),
                Style({'plot' : {'marker' : { 'label':{'fontSize': None}}}})
    )
)

slide1.add_step(
    Step(
        Config(
            {
                'size':None,
                'x': 'game_year',
                'y': 'Count',
                'geometry':'rectangle',
                'title': 'Medals per Year',
            }
        )
    )
)
# Add the slide to the story
story.add_slide(slide1)

# Create and add next slide 
# that shows components side-by-side

slide1_2 = Slide(
    Step(
        Config(
            {
                'y':['Count','game_season'],
                'color': 'game_season',
                'legend':'color',
                'label':None,
            }
        ),
        Style({'plot' : {'marker' : { 'colorPalette' : '#FAD800 #D1CFFF'}}})
    )
)
story.add_slide(slide1_2)

slide2 = Slide()

slide2.add_step(
    Step(
        Config(
            {
                'x':['game_year','game_season'],
                'y':'Count',
            }
        )
    )
)

slide2.add_step(
    Step(
        Config(
            {
                'x':['game_season','game_year'],
                'title':'Medals grouped by Season'
            }
        ),
        Style({'plot' : {'xAxis' :{ 'label' :{ 'fontSize' : '1.3em'}}}})
    )
)
story.add_slide(slide2)

slide3 = Slide(
    Step(
    Data.filter("record.game_season === 'Summer'"),
        Config({'title':'Medals in the Summer Olympics'
})
    )
)
story.add_slide(slide3)

slide4 = Slide(
    Step(
        Config(
            {
               'y':['Count','event_gender'],
                'color': 'event_gender',
                'x':'game_year',
                'label':None,
                'title':'Medals by Event Gender'
                
            }
        ),
        Style({'plot' : {'marker' : { 'colorPalette' : '#96BDFF #FF6FB1 #E4B218 #9786F1'},
                        'xAxis' :{ 'label' :{ 'fontSize' : '1.1em'}}}})
    )
)
story.add_slide(slide4)

slide4_1 = Slide(
    Step(
        Config(
            {
                'align': 'stretch',
                'label':None,
            }
        )
    )
)
story.add_slide(slide4_1)

slide5 = Slide()

slide5.add_step(Step(
        Data.filter("record.game_season === 'Summer' && record.event_gender === 'Open'"),
        Config(
            {
                'align':'none',
                'x':['Count','event_gender','game_season'],
                'y':'discipline_title',
                'legend':None,
                'sort': "byValue",
            }
        ), 
        Style({'plot':{'paddingLeft' : '14em','marker':{'label':{'position':'right','fontSize':'1.3em'}},
                      'yAxis' :{ 'label' :{ 'fontSize' : '1.3em'}}}})
    )
)

slide5.add_step(Step(
        Config(
            {
                'label':'Count',
                'title':'Medals Awarded on Open Gender Events'
            }
        )
    )
)

story.add_slide(slide5)


slide7 = Slide()

slide7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer'"),
        Config(
            {
                'x':['game_year','game_season'],
                'y':['Count','event_gender'],
                'sort': 'none',
                'label': None,
                'title':'Medals in the Summer Olympics'
            }
        ),
        Style({'plot':{'paddingLeft' : None,'marker':{'label':{'position':None, 'fontSize':None}}}})

    )
)

slide7.add_step(
    Step(
        Config(
            {
                'y':'Count',
                'color':None
            }
        ),
        Style({'plot' : {'marker' : { 'colorPalette' : '#A2A2B2'}}})
    )
)

slide7.add_step(
    Step(
        Config(
            {
                'y':['Count','medal_type'],
                'color':'medal_type',
            }
        ),
        Style({'plot' : {'marker' : { 'colorPalette' : '#D78B3F #BFBFCE #FFD700'}}})
    )
)

slide7.add_step(
    Step(
        Config(
            {
                'split':True,
            }
        )
    )
)

story.add_slide(slide7)

slide8 = Slide(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD'"),
        Config(
            {
                'align':'none',
                'split':False,
                'label':'Count',
                'title':'Gold Medals in the Summer Olympics'
            }
        ),
    )
)
story.add_slide(slide8)

slide9 = Slide()

slide9.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && record.game_year === '1896'"),
    )
)

slide9.add_step(
    Step(
        Config({
            'x':'Count',
            'y':'country_name',
            'color':'country_name',
            'sort':'byValue',
            'legend':None,
            'title':'Total Gold Medals by Country in 1896'
        }),
    Style({'plot' : {'paddingLeft' : '10em','xAxis' :{ 'label' :{ 'angle' : '0'}},
                     'marker' : { 'label':{'position':'right','fontSize':'1.3em'},'colorPalette' : '#3364B3 #DDDB2F #CC0000 #445C97 #517DFF #FF0000 #8F8745 #D46C29 #5D8866 #D0A3A3 #A2A2B2'}}})
    )
)


story.add_slide(slide9)

slide10_0 = Slide()

dur = 0.4


slide10_0.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900')"),
          Config({
            'title':'Total Gold Medals by Country in 1900',
            'y':{'range':{'min': "-9.99999max"}}
          }),        duration=0.7,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
    )
)

story.add_slide(slide10_0)

slide10 = Slide()

slide10.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904')"),
        Config({
            'title':'Total Gold Medals by Country in 1904'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
    )
)

slide10.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904')"),
        Config({
            'title':'Total Gold Medals by Country in 1904'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908')"),
        Config({
            'title':'Total Gold Medals by Country in 1908'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912')"),
        Config({
            'title':'Total Gold Medals by Country in 1912'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
story.add_slide(slide10)

slide10_1 = Slide()
slide10_1.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916')"),
        Config({
            'title':'Total Gold Medals by Country in 1916'
        })
    )
)

story.add_slide(slide10_1)

slide10_2 = Slide()
slide10_2.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920')"),
        Config({
            'title':'Total Gold Medals by Country in 1920'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_2.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924')"),
        Config({
            'title':'Total Gold Medals by Country in 1924'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_2.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928')"),
        Config({
            'title':'Total Gold Medals by Country in 1928'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_2.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932')"),
        Config({
            'title':'Total Gold Medals by Country in 1932'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_2.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936')"),
        Config({
            'title':'Total Gold Medals by Country in 1936'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
story.add_slide(slide10_2)

slide10_3 = Slide()
slide10_3.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940')"),
        Config({
            'title':'Total Gold Medals by Country in 1940'
        }),duration = 2,title={"delay": 0},
    )
)
slide10_3.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944')"),
        Config({
            'title':'Total Gold Medals by Country in 1944'
        })
    )
)
story.add_slide(slide10_3)

slide10_4 = Slide()
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948')"),
        Config({
            'title':'Total Gold Medals by Country in 1948'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952')"),
        Config({
            'title':'Total Gold Medals by Country in 1952'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956')"),
        Config({
            'title':'Total Gold Medals by Country in 1956'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960')"),
        Config({
            'title':'Total Gold Medals by Country in 1960'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964')"),
        Config({
            'title':'Total Gold Medals by Country in 1964'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968')"),
        Config({
            'title':'Total Gold Medals by Country in 1968'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972')"),
        Config({
            'title':'Total Gold Medals by Country in 1972'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_4.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976')"),
        Config({
            'title':'Total Gold Medals by Country in 1976'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)

story.add_slide(slide10_4)

slide10_5 = Slide()

slide10_5.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980')"),
        Config({
            'title':'Total Gold Medals by Country in 1980'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
story.add_slide(slide10_5)

slide10_6 = Slide()
slide10_6.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984')"),
        Config({
            'title':'Total Gold Medals by Country in 1984'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
story.add_slide(slide10_6)

slide10_7 = Slide()
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988')"),
        Config({
            'title':'Total Gold Medals by Country in 1988'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992')"),
        Config({
            'title':'Total Gold Medals by Country in 1992'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992'  || record.game_year === '1996')"),
        Config({
            'title':'Total Gold Medals by Country in 1996'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992'  || record.game_year === '1996'  || record.game_year === '2000')"),
        Config({
            'title':'Total Gold Medals by Country in 2000'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992'  || record.game_year === '1996'  || record.game_year === '2000'  || record.game_year === '2004')"),
        Config({
            'title':'Total Gold Medals by Country in 2004'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992'  || record.game_year === '1996'  || record.game_year === '2000'  || record.game_year === '2004'  || record.game_year === '2008')"),
        Config({
            'title':'Total Gold Medals by Country in 2008'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992'  || record.game_year === '1996'  || record.game_year === '2000'  || record.game_year === '2004'  || record.game_year === '2008'  || record.game_year === '2012')"),
        Config({
            'title':'Total Gold Medals by Country in 2012'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992'  || record.game_year === '1996'  || record.game_year === '2000'  || record.game_year === '2004'  || record.game_year === '2008'  || record.game_year === '2012'  || record.game_year === '2016')"),
        Config({
            'title':'Total Gold Medals by Country in 2016'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
slide10_7.add_step(
    Step(
        Data.filter("record.game_season === 'Summer' && record.medal_type === 'GOLD' && (record.game_year === '1896' || record.game_year === '1900' || record.game_year === '1904'  || record.game_year === '1908'  || record.game_year === '1912'  || record.game_year === '1916'  || record.game_year === '1920'  || record.game_year === '1924'  || record.game_year === '1928'  || record.game_year === '1932'  || record.game_year === '1936'  || record.game_year === '1940'  || record.game_year === '1944'  || record.game_year === '1948'  || record.game_year === '1952'  || record.game_year === '1956'  || record.game_year === '1960'  || record.game_year === '1964'  || record.game_year === '1968'  || record.game_year === '1972'  || record.game_year === '1976'  || record.game_year === '1980'  || record.game_year === '1984'  || record.game_year === '1988'  || record.game_year === '1992'  || record.game_year === '1996'  || record.game_year === '2000'  || record.game_year === '2004'  || record.game_year === '2008'  || record.game_year === '2012'  || record.game_year === '2016'  || record.game_year === '2020')"),
        Config({
            'title':'Total Gold Medals by Country in 2020'
        }),        duration=dur,
        x={"easing": "linear", "delay": 0},
        y={"delay": 0},
        show={"delay": 0},
        hide={"delay": 0},
        title={"duration": 0, "delay": 0},
    )
)
story.add_slide(slide10_7)

slide11 = Slide()

slide11.add_step(
    Step(
        Config(
                {
                    'x':["country_name",'Count'],
                    'label':None,
                    'color':'country_name',
                    "y": {'set':None,'range': { 'min':-2, 'max':1}},
                    'coordSystem':'polar',
                }
            ),
        Style({'plot':{'marker':{'label':{'position':'top'}}}})

    )
)

slide11.add_step(
    Step(
        Config(
                {
                    'x':["top10C",'Count'],
                    'label':"top10C",
                    'color':'top10C',
                }
            )
    )
)
story.add_slide(slide11)

# Switch on the tooltip that appears 
# when the user hovers the mouse over a chart element.
story.set_feature('tooltip', True)
# Play the created story
story.play()


# Visit [ipyvizzu.com](http://ipyvizzzu.com) to learn more!

In [29]:
# Make exported story full-screen by setting vertical size to 100%
# Export the story as an HTML file

story.set_size('100%', '100%')
story.export_to_html(filename='Olympics.html')